In [1]:
import datetime as dt

import matplotlib.pyplot as plt
import mplfinance as mpf
import numpy as np
import pandas as pd
import pandas_market_calendars as mcal
import plotly.graph_objects as go
import polars as pl
from dash import Dash, dcc, html
from plotly.subplots import make_subplots

nse = mcal.get_calendar("NSE")

pd.set_option("display.max_rows", 25_000)
pd.set_option("display.max_columns", 500)
pl.Config.set_tbl_cols(500)
pl.Config.set_tbl_rows(10_000)
pd.options.display.float_format = "{:.4f}".format

import sys

sys.path.append("..")
from tooling.enums import AssetClass, Index, Spot, StrikeSpread
from tooling.fetch import fetch_option_data, fetch_spot_data
from tooling.filter import find_atm, option_tool

from fetching_from_local_db.enums import AssetClass, Index, StrikeSpread
from fetching_from_local_db.fetch_from_db import _fetch_batch, fetch_data, fetch_spot_data

In [2]:
bnf = pd.read_csv('../data/BNF_LONG_TB Correlation check JJSU.csv')
nifty = pd.read_csv('../data/NF_LONG_TB Correlation check JJSU.csv')
fnf = pd.read_csv('../data/FNF_LONG_TB Correlation check JJSU.csv')
midcp_l = pd.read_csv('../data/MIDCP_LONG_TB Correlation check JJSU.csv')
midcp_s = pd.read_csv('../data/MIDCP_SHORT_TB Correlation check JJSU.csv')

# df1 = pd.read_csv('FNF1.csv')
# df2 = pd.read_csv('FNF2.csv')

# print((bnf.head()).to_string())
# print((nifty.head()).to_string())

In [3]:
combined_df = pd.concat([midcp_l, midcp_s], ignore_index=True)
combined_df.drop(columns=['Unnamed: 0'], inplace=True)
combined_df['Entry Time'] = pd.to_datetime(combined_df['Entry Time'])
combined_df = combined_df.sort_values(by='Entry Time')
midcp = combined_df

In [4]:
midcp = midcp.dropna(subset=['DD%'])
midcp

DATETIME  TODAYS OPEN  TODAYS CLOSE  POINTS CAPTURED TODAY  QTY  MTM  \
614       NaN          NaN           NaN                    NaN  NaN  NaN   
616       NaN          NaN           NaN                    NaN  NaN  NaN   
622       NaN          NaN           NaN                    NaN  NaN  NaN   
625       NaN          NaN           NaN                    NaN  NaN  NaN   
628       NaN          NaN           NaN                    NaN  NaN  NaN   
637       NaN          NaN           NaN                    NaN  NaN  NaN   
640       NaN          NaN           NaN                    NaN  NaN  NaN   
642       NaN          NaN           NaN                    NaN  NaN  NaN   
644       NaN          NaN           NaN                    NaN  NaN  NaN   
647       NaN          NaN           NaN                    NaN  NaN  NaN   
649       NaN          NaN           NaN                    NaN  NaN  NaN   
652       NaN          NaN           NaN                    NaN  NaN  NaN   
657       NaN          NaN           NaN                    NaN  NaN  NaN   
683       NaN          NaN           NaN                    NaN  NaN  NaN   
686       NaN          NaN           NaN                    NaN  NaN  NaN   
689       NaN          NaN           NaN                    NaN  NaN  NaN   
693       NaN          NaN           NaN                    NaN  NaN  NaN   
695       NaN          NaN           NaN                    NaN  NaN  NaN   
699       NaN          NaN           NaN                    NaN  NaN  NaN   
704       NaN          NaN           NaN                    NaN  NaN  NaN   
713       NaN          NaN           NaN                    NaN  NaN  NaN   
715       NaN          NaN           NaN                    NaN  NaN  NaN   
718       NaN          NaN           NaN                    NaN  NaN  NaN   
721       NaN          NaN           NaN                    NaN  NaN  NaN   
731       NaN          NaN           NaN                    NaN  NaN  NaN   
734       NaN          NaN           NaN                    NaN  NaN  NaN   
736       NaN          NaN           NaN                    NaN  NaN  NaN   
771       NaN          NaN           NaN                    NaN  NaN  NaN   
774       NaN          NaN           NaN                    NaN  NaN  NaN   
777       NaN          NaN           NaN                    NaN  NaN  NaN   
790       NaN          NaN           NaN                    NaN  NaN  NaN   
792       NaN          NaN           NaN                    NaN  NaN  NaN   
795       NaN          NaN           NaN                    NaN  NaN  NaN   
797       NaN          NaN           NaN                    NaN  NaN  NaN   
800       NaN          NaN           NaN                    NaN  NaN  NaN   
808       NaN          NaN           NaN                    NaN  NaN  NaN   
810       NaN          NaN           NaN                    NaN  NaN  NaN   
814       NaN          NaN           NaN                    NaN  NaN  NaN   
816       NaN          NaN           NaN                    NaN  NaN  NaN   
825       NaN          NaN           NaN                    NaN  NaN  NaN   
840       NaN          NaN           NaN                    NaN  NaN  NaN   
844       NaN          NaN           NaN                    NaN  NaN  NaN   
846       NaN          NaN           NaN                    NaN  NaN  NaN   
849       NaN          NaN           NaN                    NaN  NaN  NaN   
851       NaN          NaN           NaN                    NaN  NaN  NaN   
860       NaN          NaN           NaN                    NaN  NaN  NaN   
863       NaN          NaN           NaN                    NaN  NaN  NaN   
866       NaN          NaN           NaN                    NaN  NaN  NaN   
870       NaN          NaN           NaN                    NaN  NaN  NaN   
872       NaN          NaN           NaN                    NaN  NaN  NaN   
874       NaN          NaN           NaN                    NaN  NaN  NaN   
8

In [5]:
bnf = bnf.dropna(subset=['Signal Generated At'])
nifty = nifty.dropna(subset=['Signal Generated At'])
fnf = fnf.dropna(subset=['Signal Generated At'])

In [6]:
combined_df.loc[combined_df['Entry Time'].dt.year < 2022, 'ROI%'] = combined_df['ROI%'] / 3
combined_df.loc[combined_df['Entry Time'].dt.year >= 2022, 'ROI%'] = combined_df['ROI%'] / 4

In [11]:
combined_df.head()

DATETIME  TODAYS OPEN  TODAYS CLOSE  POINTS CAPTURED TODAY  QTY  MTM  \
1        NaN          NaN           NaN                    NaN  NaN  NaN   
614      NaN          NaN           NaN                    NaN  NaN  NaN   
3        NaN          NaN           NaN                    NaN  NaN  NaN   
616      NaN          NaN           NaN                    NaN  NaN  NaN   
9        NaN          NaN           NaN                    NaN  NaN  NaN   

     Signal Generated At Trade Type          Entry Time  Entry Price  \
1    2022-01-11 11:15:00       LONG 2022-01-11 12:15:00    7784.8500   
614  2022-01-11 11:15:00       LONG 2022-01-11 12:15:00    7784.8500   
3    2022-01-12 10:15:00       LONG 2022-01-12 11:15:00    7831.0000   
616  2022-01-12 10:15:00       LONG 2022-01-12 11:15:00    7831.0000   
9    2022-01-12 13:15:00       LONG 2022-01-12 14:15:00    7856.9000   

     Initial SL  Final SL            Exit Time  Exit Price  Points Captured  \
1     7763.6500 7763.6500  2022-01-11 14:15:00   7763.6500         -21.2000   
614   7763.6500 7763.6500  2022-01-11 14:15:00   7763.6500         -21.2000   
3     7815.6500 7815.6500  2022-01-12 11:15:00   7815.6500         -15.3500   
616   7815.6500 7815.6500  2022-01-12 11:15:00   7815.6500         -15.3500   
9     7831.0500 7831.0500  2022-01-18 14:15:00   7831.0500         -25.8500   

     After Costs    THEO PnL         Remarks      Qty    ROI%  Trade Year  \
1       -28.9743 -20424.2856  Initial SL Hit 963.4097 -0.6979   2022.0000   
614     -28.9743 -20424.2856  Initial SL Hit 963.4097 -0.6979   2022.0000   
3       -23.1733 -14701.1876  Initial SL Hit 957.7321 -0.5548   2022.0000   
616     -23.1733 -14701.1876  Initial SL Hit 957.7321 -0.5548   2022.0000   
9       -33.6940 -24675.7627  Initial SL Hit 954.5750 -0.8041   2022.0000   

     Trade Month     DD%  
1         1.0000     NaN  
614       1.0000  0.0000  
3         1.0000     NaN  
616       1.0000 -2.2194  
9         1.0000     NaN

In [7]:
opt_buy = pd.read_csv('BNF_FNF_NF_MIDCP_Combined_MTrend_Opt_Buying.csv')
combined_df = pd.concat([bnf, fnf, nifty, midcp], ignore_index=True)
combined_df.drop(columns=['Unnamed: 0'], inplace=True)
combined_df['Entry Time'] = pd.to_datetime(combined_df['Entry Time'])
combined_df = combined_df.sort_values(by='Entry Time')

FileNotFoundError: [Errno 2] No such file or directory: 'BNF_FNF_NF_MIDCP_Combined_MTrend_Opt_Buying.csv'

In [8]:
combined_df

DATETIME  TODAYS OPEN  TODAYS CLOSE  POINTS CAPTURED TODAY       QTY  \
1            NaN          NaN           NaN                    NaN       NaN   
614          NaN          NaN           NaN                    NaN       NaN   
3            NaN          NaN           NaN                    NaN       NaN   
616          NaN          NaN           NaN                    NaN       NaN   
9            NaN          NaN           NaN                    NaN       NaN   
622          NaN          NaN           NaN                    NaN       NaN   
12           NaN          NaN           NaN                    NaN       NaN   
625          NaN          NaN           NaN                    NaN       NaN   
15           NaN          NaN           NaN                    NaN       NaN   
628          NaN          NaN           NaN                    NaN       NaN   
24           NaN          NaN           NaN                    NaN       NaN   
637          NaN          NaN           NaN                    NaN       NaN   
27           NaN          NaN           NaN                    NaN       NaN   
640          NaN          NaN           NaN                    NaN       NaN   
642          NaN          NaN           NaN                    NaN       NaN   
29           NaN          NaN           NaN                    NaN       NaN   
644          NaN          NaN           NaN                    NaN       NaN   
31           NaN          NaN           NaN                    NaN       NaN   
647          NaN          NaN           NaN                    NaN       NaN   
34           NaN          NaN           NaN                    NaN       NaN   
649          NaN          NaN           NaN                    NaN       NaN   
36           NaN          NaN           NaN                    NaN       NaN   
652          NaN          NaN           NaN                    NaN       NaN   
39           NaN          NaN           NaN                    NaN       NaN   
44           NaN          NaN           NaN                    NaN       NaN   
657          NaN          NaN           NaN                    NaN       NaN   
683          NaN          NaN           NaN                    NaN       NaN   
70           NaN          NaN           NaN                    NaN       NaN   
73           NaN          NaN           NaN                    NaN       NaN   
686          NaN          NaN           NaN                    NaN       NaN   
689          NaN          NaN           NaN                    NaN       NaN   
76           NaN          NaN           NaN                    NaN       NaN   
693          NaN          NaN           NaN                    NaN       NaN   
80           NaN          NaN           NaN                    NaN       NaN   
695          NaN          NaN           NaN                    NaN       NaN   
82           NaN          NaN           NaN                    NaN       NaN   
86           NaN          NaN           NaN                    NaN       NaN   
699          NaN          NaN           NaN                    NaN       NaN   
91           NaN          NaN           NaN                    NaN       NaN   
704          NaN          NaN           NaN                    NaN       NaN   
100          NaN          NaN           NaN                    NaN       NaN   
713          NaN          NaN           NaN                    NaN       NaN   
715          NaN          NaN           NaN                    NaN       NaN   
102          NaN          NaN           NaN                    NaN       NaN   
105          NaN          NaN           NaN                    NaN       NaN   
718          NaN          NaN           NaN                    NaN       NaN   
108          NaN          NaN           NaN                    NaN       NaN   
721          NaN          NaN           NaN                    NaN       NaN   
118          NaN          NaN           NaN                    NaN       NaN   
731     

In [9]:
# combined_df = combined_df.drop(columns=['DATETIME', 'TODAYS OPEN', 'TODAYS CLOSE', 'POINTS CAPTURED TODAY', 'QTY', 'MTM', 'DD%'])
combined_df['PnL'] = np.where(combined_df['Strategy'].isna(), 'OPT BUY', 'POSITIONAL')

KeyError: 'Strategy'

In [47]:
combined_df2.to_csv('Combined MTrend Shotgun.csv')

In [43]:
combined_df2 = pd.concat([combined_df, opt_buy], ignore_index=True)
combined_df2.drop(columns=['Unnamed: 0'], inplace=True)
combined_df2['Entry Time'] = pd.to_datetime(combined_df2['Entry Time'])
combined_df2 = combined_df2.sort_values(by='Entry Time')
combined_df2 = combined_df2.drop(columns=['DATETIME', 'TODAYS OPEN', 'TODAYS CLOSE', 'POINTS CAPTURED TODAY', 'QTY', 'MTM', 'DD%'])
combined_df2['Strategy'] = np.where(combined_df2['THEO PnL'].isna(), 'OPT BUY', 'POSITIONAL')

In [53]:
combined_df2

Signal Generated At Trade Type          Entry Time  Entry Price  \
1527  2017-01-05 14:00:00        BUY 2017-01-05 14:05:00      34.9500   
0     2017-01-09 10:15:00       LONG 2017-01-09 11:15:00    8246.5500   
1     2017-01-11 10:15:00       LONG 2017-01-11 11:15:00   18670.8500   
2     2017-01-17 12:15:00       LONG 2017-01-17 13:15:00    7622.5500   
3     2017-01-19 10:15:00       LONG 2017-01-19 11:15:00   19108.4000   
4     2017-01-20 10:15:00       LONG 2017-01-20 11:15:00    7572.1000   
5     2017-01-20 10:15:00       LONG 2017-01-20 11:15:00   19010.5000   
6     2017-01-20 15:15:00       LONG 2017-01-23 09:15:00    7509.9000   
7     2017-01-23 13:15:00       LONG 2017-01-23 14:15:00    7511.3000   
8     2017-01-24 11:15:00       LONG 2017-01-24 12:15:00   18977.7500   
9     2017-01-24 12:15:00       LONG 2017-01-24 13:15:00    8445.3000   
10    2017-01-24 13:15:00       LONG 2017-01-24 14:15:00   19013.1500   
11    2017-01-24 14:15:00       LONG 2017-01-24 15:15:00    8476.1000   
1528  2017-01-25 13:30:00        BUY 2017-01-25 13:35:00      10.9500   
1529  2017-01-25 14:00:00        BUY 2017-01-25 14:05:00      15.1500   
1530  2017-01-25 14:10:00        BUY 2017-01-25 14:15:00      10.5500   
1531  2017-01-25 14:20:00        BUY 2017-01-25 14:25:00      11.3500   
1532  2017-01-25 14:50:00        BUY 2017-01-25 14:55:00      21.5000   
12    2017-01-31 11:15:00       LONG 2017-01-31 12:15:00   19492.3000   
13    2017-01-31 15:15:00       LONG 2017-02-01 09:15:00   19543.4500   
14    2017-02-01 12:15:00       LONG 2017-02-01 13:15:00   19941.7000   
15    2017-02-01 12:15:00       LONG 2017-02-01 13:15:00    8658.8000   
1533  2017-02-02 14:00:00        BUY 2017-02-02 14:05:00      54.8000   
1534  2017-02-02 14:25:00        BUY 2017-02-02 14:30:00      29.0000   
16    2017-02-08 12:15:00       LONG 2017-02-08 13:15:00   20297.3000   
17    2017-02-08 14:15:00       LONG 2017-02-08 15:15:00   20300.1000   
19    2017-02-09 11:15:00       LONG 2017-02-09 12:15:00   20108.3000   
18    2017-02-09 11:15:00       LONG 2017-02-09 12:15:00    8755.5500   
20    2017-02-13 12:15:00       LONG 2017-02-13 13:15:00   20194.2000   
21    2017-02-13 13:15:00       LONG 2017-02-13 14:15:00    8803.8000   
22    2017-02-14 12:15:00       LONG 2017-02-14 13:15:00   20228.7500   
23    2017-02-16 10:15:00       LONG 2017-02-16 11:15:00    8144.6500   
1535  2017-02-16 13:55:00        BUY 2017-02-16 14:00:00      29.1500   
25    2017-02-17 10:15:00       LONG 2017-02-17 11:15:00    8836.8000   
24    2017-02-17 10:15:00       LONG 2017-02-17 11:15:00   20707.2000   
26    2017-02-20 09:15:00       LONG 2017-02-20 10:15:00   20560.8000   
27    2017-02-20 10:15:00       LONG 2017-02-20 11:15:00    8840.7000   
1536  2017-02-23 13:40:00        BUY 2017-02-23 13:45:00       8.3500   
28    2017-02-27 10:15:00       LONG 2017-02-27 11:15:00   20730.3500   
29    2017-02-27 15:15:00       LONG 2017-02-28 09:15:00   20632.2500   
30    2017-02-28 11:15:00       LONG 2017-02-28 12:15:00    8894.5000   
31    2017-02-28 13:15:00       LONG 2017-02-28 14:15:00   20614.4000   
32    2017-03-01 11:15:00       LONG 2017-03-01 12:15:00    8936.7500   
33    2017-03-01 13:15:00       LONG 2017-03-01 14:15:00    8942.4500   
1537  2017-03-02 14:10:00        BUY 2017-03-02 14:15:00       6.5000   
34    2017-03-03 12:15:00       LONG 2017-03-03 13:15:00    8241.7500   
35    2017-03-06 09:15:00       LONG 2017-03-06 10:15:00    8960.2500   
36    2017-03-08 14:15:00       LONG 2017-03-08 15:15:00   20687.1500   
37    2017-03-09 10:15:00       LONG 2017-03-09 11:15:00   20705.3500   
38    2017-03-09 12:15:00       LONG 2017-03-09 13:15:00    8915.2000   
39    2017-03-09 13:15:00       LONG 2017-03-09 14:15:00   20697.8000   
40    2017-03-10 11:15:00       LONG 2017-03-10 12:15:00    8941.8000   
41    2017-03-14 10:15:00       LONG 2017-03-14 11:15:00    8516.5500   
42    2017-03-14 10:15:00       LONG 2017-03-14 11:15:00   21180

In [45]:
combined_df2 = combined_df2.drop(columns=['Drawdown', 'Cumulative ROI%', 'Running Max ROI%'])

In [48]:
combined_df2['entry_date'] = np.where(combined_df2['Expiry'].isna(), combined_df2['Entry Time'].dt.date, combined_df2['Expiry'])

In [56]:
def generate_stats(tb):
    stats_df8 = pd.DataFrame(
        index=range(2017, 2025),
        columns=[
            "Total ROI",
            "Total Trades",
            "Win Rate",
            "Avg Profit% per Trade",
            "Avg Loss% per Trade",
            "Max Drawdown",
            "ROI/DD Ratio",
        ],
    )
    combined_df_sorted = tb
    
    # Iterate over each year
    for year in range(2017, 2025):
        # Filter trades for the current year
        year_trades = combined_df_sorted[(combined_df_sorted["Trade Year"] == year)]
    
        # Calculate total ROI
        total_roi = year_trades["ROI%"].sum()
    
        # Calculate total number of trades
        total_trades = len(year_trades)
    
        # Calculate win rate
        win_rate = (year_trades["ROI%"] > 0).mean() * 100
    
        # Calculate average profit per trade
        avg_profit = year_trades[year_trades["ROI%"] > 0]["ROI%"].mean()
    
        # Calculate average loss per trade
        avg_loss = year_trades[year_trades["ROI%"] < 0]["ROI%"].mean()
    
        # Calculate maximum drawdown
        max_drawdown = (
            year_trades["ROI%"].cumsum() - year_trades["ROI%"].cumsum().cummax()
        ).min()
    
        # Calculate ROI/DD ratio
        roi_dd_ratio = total_roi / abs(max_drawdown)
    
        # Store the statistics in the DataFrame
        stats_df8.loc[year] = [
            total_roi,
            total_trades,
            win_rate,
            avg_profit,
            avg_loss,
            max_drawdown,
            roi_dd_ratio,
        ]
    
    # Calculate overall statistics
    overall_total_roi = stats_df8["Total ROI"].sum()
    overall_total_trades = stats_df8["Total Trades"].sum()
    overall_win_rate = (combined_df_sorted["ROI%"] > 0).mean() * 100
    overall_avg_profit = combined_df_sorted[combined_df_sorted["ROI%"] > 0]["ROI%"].mean()
    overall_avg_loss = combined_df_sorted[combined_df_sorted["ROI%"] < 0]["ROI%"].mean()
    overall_max_drawdown = (
        combined_df_sorted["ROI%"].cumsum() - combined_df_sorted["ROI%"].cumsum().cummax()
    ).min()
    overall_roi_dd_ratio = overall_total_roi / abs(overall_max_drawdown)
    
    # Store the overall statistics in the DataFrame
    stats_df8.loc["Overall"] = [
        overall_total_roi,
        overall_total_trades,
        overall_win_rate,
        overall_avg_profit,
        overall_avg_loss,
        overall_max_drawdown,
        overall_roi_dd_ratio,
    ]
    return stats_df8

In [57]:
stats = generate_stats(combined_df2)
stats

Total ROI Total Trades Win Rate Avg Profit% per Trade  \
2017     168.1720          288  30.5556                3.5791   
2018     100.4955          252  29.3651                3.3986   
2019     160.7320          287  30.6620                3.6730   
2020     314.4312          288  34.7222                5.2556   
2021     146.6595          290  31.0345                3.8227   
2022     156.8199          350  30.0000                3.5645   
2023     331.2525          475  31.1579                3.7852   
2024      75.8453          183  24.5902                4.3108   
Overall 1454.4078    2413.0000  30.5843                3.9129   

        Avg Loss% per Trade Max Drawdown ROI/DD Ratio  
2017                -0.7340     -21.2365       7.9190  
2018                -0.8483     -30.9194       3.2502  
2019                -0.8165     -19.0654       8.4306  
2020                -1.1230     -32.4300       9.6957  
2021                -0.9869     -22.4704       6.5268  
2022                -0.8876     -29.9541       5.2353  
2023                -0.7002     -38.1081       8.6924  
2024                -0.8561     -27.6240       2.7456  
Overall             -0.8557     -38.8128      37.4723

# MTrend + Shotgun Combined Stats
## MTrend 1.5x Lev , Shotgun 1% RPT